# Amazon Review Analysis

Data source: https://snap.stanford.edu/data/web-FineFoods.html

Useful resources: 
- PySpark cheat sheet: http://web.utk.edu/~wfeng1/doc/cheatSheet_pyspark.pdf
- MLlib document: https://spark.apache.org/docs/latest/ml-guide.html
- SparkR document: https://spark.apache.org/docs/latest/sparkr.html
- SparkR tutorial: https://rpubs.com/wendyu/sparkr

## Before We Start...

Basic concepts of Spark: 
- RDD (Resilient Distributed Datasets): fundamental data structure for distributing data among cluster nodes. Immutable.
- Transformation: operations on RDD that returns an RDD, such as map, filter, reduce, and reduceByKey.
- Action: operations on RDD that returns a non-RDD value, such as collect.

We will be mainly using Spark Dataframe APIs instead of RDD APIs, to simplify development.
- Spark Dataframes are very similar to tables in relational databases. They have schema. Most of the operations on them are similar to querying a relational database as well. You can consider Spark Dataframe as a wrap on top of RDD.

## Loading Data

In [4]:
%run "./Data Lake Connection"

In [5]:
# Reading data from Azure Data Lake

from pyspark.sql.types import *

amazon_schema = StructType([StructField('Id',IntegerType(),True), 
                            StructField('ProductId',StringType(),True),
                            StructField('UserId',StringType(),True),
                            StructField('ProfileName',StringType(),True),
                            StructField('HelpfulnessNumerator',IntegerType(),True),
                            StructField('HelpfulnessDenominator',IntegerType(),True),
                            StructField('Score',IntegerType(),True),
                            StructField('Time',IntegerType(),True),
                            StructField('Summary',StringType(),True),
                            StructField('Text',StringType(),True)])

amazon_review = spark.read.csv("abfss://data@ssbdatalakegen2.dfs.core.windows.net/Reviews.csv", header=True, schema=amazon_schema)

In [6]:
display(amazon_review)

Id ProductId UserId ProfileName HelpfulnessNumerator HelpfulnessDenominator Score Time Summary Text 1 B001E4KFG0 A3SGXH7AUHU8GW delmartian 1 1 5 1303862400 Good Quality Dog Food I have bought several of the Vitality canned dog food products and have found them all to be of good quality. The product looks more like a stew than a processed meat and it smells better. My Labrador is finicky and she appreciates this product better than most. 2 B00813GRG4 A1D87F6ZCVE5NK dll pa 0 0 1 1346976000 Not as Advertised "Product arrived labeled as Jumbo Salted Peanuts...the peanuts were actually small sized unsalted. Not sure if this was an error or if the vendor intended to represent the product as ""Jumbo""." 3 B000LQOCH0 ABXLMWJIXXAIN "Natalia Corres ""Natalia Corres""" 1 1 4 1219017600 """Delight"" says it all" "This is a confection that has been around a few centuries. It is a light, pillowy citrus gelatin with nuts - in this case Filberts. And it is cut into tiny squares and then liberally coated with powdered sugar. And it is a tiny mouthful of heaven. Not too chewy, and very flavorful. I highly recommend this yummy treat. If you are familiar with the story of C.S. Lewis' ""The Lion 4 B000UA0QIQ A395BORC6FGVXV Karl 3 3 2 1307923200 Cough Medicine If you are looking for the secret ingredient in Robitussin I believe I have found it. I got this in addition to the Root Beer Extract I ordered (which was good) and made some cherry soda. The flavor is very medicinal. 5 B006K2ZZ7K A1UQRSCLF8GW1T "Michael D. Bigham ""M. Wassir""" 0 0 5 1350777600 Great taffy Great taffy at a great price. There was a wide assortment of yummy taffy. Delivery was very quick. If your a taffy lover, this is a deal. 6 B006K2ZZ7K ADT0SRK1MGOEU Twoapennything 0 0 4 1342051200 Nice Taffy I got a wild hair for taffy and ordered this five pound bag. The taffy was all very enjoyable with many flavors: watermelon, root beer, melon, peppermint, grape, etc. My only complaint is there was a bit too much red/black licorice-flavored pieces (just not my particular favorites). Between me, my kids, and my husband, this lasted only two weeks! I would recommend this brand of taffy -- it was a delightful treat. 7 B006K2ZZ7K A1SP2KVKFXXRU1 David C. Sullivan 0 0 5 1340150400 Great! Just as good as the expensive brands! This saltwater taffy had great flavors and was very soft and chewy. Each candy was individually wrapped well. None of the candies were stuck together, which did happen in the expensive version, Fralinger's. Would highly recommend this candy! I served it at a beach-themed party and everyone loved it! 8 B006K2ZZ7K A3JRGQVEQN31IQ Pamela G. Williams 0 0 5 1336003200 Wonderful, tasty taffy This taffy is so good. It is very soft and chewy. The flavors are amazing. I would definitely recommend you buying it. Very satisfying!! 9 B000E7L2R4 A1MZYO9TZK0BBI R. James 1 1 5 1322006400 Yay Barley Right now I'm mostly just sprouting this so my cats can eat the grass. They love it. I rotate it around with Wheatgrass and Rye too 10 B00171APVA A21BT40VZCCYT4 Carol A. Reed 0 0 5 1351209600 Healthy Dog Food This is a very healthy dog food. Good for their digestion. Also good for small puppies. My dog eats her required amount at every feeding. 11 B0001PB9FE A3HDKO7OW0QNK4 Canadian Fan 1 1 5 1107820800 The Best Hot Sauce in the World I don't know if it's the cactus or the tequila or just the unique combination of ingredients, but the flavour of this hot sauce makes it one of a kind! We picked up a bottle once on a trip we were on and brought it back home with us and were totally blown away! When we realized that we simply couldn't find it anywhere in our city we were bummed. Now, because of the magic of the internet, we have a case of the sauce and are ecstatic because of it. If you love hot sauce..I mean really love hot sauce, but don't want a sauce that tastelessly burns your throat, grab a bottle of Tequila Picante Gourmet de Inclan. Just realize that once you taste it, you will never want

In [7]:
# Spark SQL

amazon_review.createOrReplaceTempView("amazon_review")
display(spark.sql("SELECT * FROM amazon_review"))

Id ProductId UserId ProfileName HelpfulnessNumerator HelpfulnessDenominator Score Time Summary Text 1 B001E4KFG0 A3SGXH7AUHU8GW delmartian 1 1 5 1303862400 Good Quality Dog Food I have bought several of the Vitality canned dog food products and have found them all to be of good quality. The product looks more like a stew than a processed meat and it smells better. My Labrador is finicky and she appreciates this product better than most. 2 B00813GRG4 A1D87F6ZCVE5NK dll pa 0 0 1 1346976000 Not as Advertised "Product arrived labeled as Jumbo Salted Peanuts...the peanuts were actually small sized unsalted. Not sure if this was an error or if the vendor intended to represent the product as ""Jumbo""." 3 B000LQOCH0 ABXLMWJIXXAIN "Natalia Corres ""Natalia Corres""" 1 1 4 1219017600 """Delight"" says it all" "This is a confection that has been around a few centuries. It is a light, pillowy citrus gelatin with nuts - in this case Filberts. And it is cut into tiny squares and then liberally coated with powdered sugar. And it is a tiny mouthful of heaven. Not too chewy, and very flavorful. I highly recommend this yummy treat. If you are familiar with the story of C.S. Lewis' ""The Lion 4 B000UA0QIQ A395BORC6FGVXV Karl 3 3 2 1307923200 Cough Medicine If you are looking for the secret ingredient in Robitussin I believe I have found it. I got this in addition to the Root Beer Extract I ordered (which was good) and made some cherry soda. The flavor is very medicinal. 5 B006K2ZZ7K A1UQRSCLF8GW1T "Michael D. Bigham ""M. Wassir""" 0 0 5 1350777600 Great taffy Great taffy at a great price. There was a wide assortment of yummy taffy. Delivery was very quick. If your a taffy lover, this is a deal. 6 B006K2ZZ7K ADT0SRK1MGOEU Twoapennything 0 0 4 1342051200 Nice Taffy I got a wild hair for taffy and ordered this five pound bag. The taffy was all very enjoyable with many flavors: watermelon, root beer, melon, peppermint, grape, etc. My only complaint is there was a bit too much red/black licorice-flavored pieces (just not my particular favorites). Between me, my kids, and my husband, this lasted only two weeks! I would recommend this brand of taffy -- it was a delightful treat. 7 B006K2ZZ7K A1SP2KVKFXXRU1 David C. Sullivan 0 0 5 1340150400 Great! Just as good as the expensive brands! This saltwater taffy had great flavors and was very soft and chewy. Each candy was individually wrapped well. None of the candies were stuck together, which did happen in the expensive version, Fralinger's. Would highly recommend this candy! I served it at a beach-themed party and everyone loved it! 8 B006K2ZZ7K A3JRGQVEQN31IQ Pamela G. Williams 0 0 5 1336003200 Wonderful, tasty taffy This taffy is so good. It is very soft and chewy. The flavors are amazing. I would definitely recommend you buying it. Very satisfying!! 9 B000E7L2R4 A1MZYO9TZK0BBI R. James 1 1 5 1322006400 Yay Barley Right now I'm mostly just sprouting this so my cats can eat the grass. They love it. I rotate it around with Wheatgrass and Rye too 10 B00171APVA A21BT40VZCCYT4 Carol A. Reed 0 0 5 1351209600 Healthy Dog Food This is a very healthy dog food. Good for their digestion. Also good for small puppies. My dog eats her required amount at every feeding. 11 B0001PB9FE A3HDKO7OW0QNK4 Canadian Fan 1 1 5 1107820800 The Best Hot Sauce in the World I don't know if it's the cactus or the tequila or just the unique combination of ingredients, but the flavour of this hot sauce makes it one of a kind! We picked up a bottle once on a trip we were on and brought it back home with us and were totally blown away! When we realized that we simply couldn't find it anywhere in our city we were bummed. Now, because of the magic of the internet, we have a case of the sauce and are ecstatic because of it. If you love hot sauce..I mean really love hot sauce, but don't want a sauce that tastelessly burns your throat, grab a bottle of Tequila Picante Gourmet de Inclan. Just realize that once you taste it, you will never want

## Cleaning Data

In [9]:
# Drop duplicates

amazon_review = amazon_review.dropDuplicates(['UserId','ProductId'])

In [10]:
# Convert Unix timestamp to readable date

from pyspark.sql.functions import from_unixtime, to_date

amazon_review = amazon_review.withColumn("Date", to_date(from_unixtime(amazon_review.Time)))

As comparison, for pandas dataframe you will use .apply() to apply a function to a column. See: https://pandas.pydata.org/pandas-docs/stable/reference/api/pandas.DataFrame.apply.html

For example: amz_review['Date'] = amz_review['Time'].apply(to_date)

In [12]:
# Tokenization

from pyspark.sql.functions import udf

def tokenize(col):
  if col is None:
    return []
  return col.split()

tokenize_udf = udf(tokenize, ArrayType(StringType()))
amazon_review = amazon_review.withColumn("WordList", tokenize_udf(amazon_review.Text))

In [13]:
# Remove special characters and partially scraped html

special_char_list=['<span','<br','\\','`','\"',"'",'*','_','{','}','[',']','(',')',';','@','^','&','>','#','+',':','-','_','=','|','>','<','~','.','!','$','/',',','?','%','0','1','2','3','4','5','6','7','8','9']

def remove_specialchar(col):
  result = []
  for word in col:
    tmp_word = word.lower()
    for special_char in special_char_list:
      tmp_word = tmp_word.replace(special_char, "")
    result.append(tmp_word)
  return result

remove_specialchar_udf = udf(remove_specialchar, ArrayType(StringType()))
amazon_review = amazon_review.withColumn("WordListCleaned", remove_specialchar_udf(amazon_review.WordList))

In [14]:
# Remove stop words

from stop_words import get_stop_words

stop_words = get_stop_words('en')
remove_stopword_udf = udf(lambda col: [w for w in col if not (w in stop_words)], ArrayType(StringType()))
amazon_review = amazon_review.withColumn("WordListCleaned", remove_stopword_udf(amazon_review.WordListCleaned))

In [15]:
# Stemming

from nltk.stem.porter import PorterStemmer

p_stemmer = PorterStemmer()
stemming_udf = udf(lambda col: [p_stemmer.stem(w) for w in col], ArrayType(StringType()))
amazon_review = amazon_review.withColumn("WordListCleaned", stemming_udf(amazon_review.WordListCleaned))

In [16]:
display(amazon_review)

Id ProductId UserId ProfileName HelpfulnessNumerator HelpfulnessDenominator Score Time Summary Text Date WordList WordListCleaned 290915 B005HG9ESG #oc-R1OE1OPY34LOC8 D 0 0 3 1344902400 Not the same Been buying this water for a couple of years. They recently changed the packaging and for some reason or other, the water seems different. The same clean taste is just NOT there. Not buying it again. 2012-08-14 List(Been, buying, this, water, for, a, couple, of, years., They, recently, changed, the, packaging, and, for, some, reason, or, other,, the, water, seems, different., The, same, clean, taste, is, just, NOT, there., Not, buying, it, again.) List(buy, water, coupl, year, recent, chang, packag, reason, water, seem, differ, clean, tast, just, buy) 136337 B006Q820X0 #oc-R39HI2LQ9LHV32 stephanie 1 2 1 1339632000 Kcups leaking and coffee tasted old The kcups looked okay, but many of them sprayed coffee on the counter, had coffee grounds coming out. I won't buy this again. 2012-06-14 List(The, kcups, looked, okay,, but, many, of, them, sprayed, coffee, on, the, counter,, had, coffee, grounds, coming, out., I, won't, buy, this, again.) List(kcup, look, okay, mani, spray, coffe, counter, coffe, ground, come, wont, buy) 124400 B005ZBZM52 #oc-R8EZLM74R071X jalien 0 0 1 1350172800 Great design, not so great flavor I wanted to try something new and this is new alright. While I love and appreciate the design, the flavor is less than desirable. It's too bitter. I drink my coffee black and really enjoy a strong cup of dark roast, but after discovering I didn't care for the flavor, I tried to disguise it with the flavor of creamer I knew I'd like (coconut cream, yum) and still the flavor of the bitter coffee was just too much. 2012-10-14 List(I, wanted, to, try, something, new, and, this, is, new, alright., While, I, love, and, appreciate, the, design,, the, flavor, is, less, than, desirable., It's, too, bitter., I, drink, my, coffee, black, and, really, enjoy, a, strong, cup, of, dark, roast,, but, after, discovering, I, didn't, care, for, the, flavor,, I, tried, to, disguise, it, with, the, flavor, of, creamer, I, knew, I'd, like, (coconut, cream,, yum), and, still, the, flavor, of, the, bitter, coffee, was, just, too, much.) List(want, tri, someth, new, new, alright, love, appreci, design, flavor, less, desir, bitter, drink, coffe, black, realli, enjoy, strong, cup, dark, roast, discov, didnt, care, flavor, tri, disguis, flavor, creamer, knew, id, like, coconut, cream, yum, still, flavor, bitter, coffe, just, much) 345714 B000ED9L9E A10103MJIKKIFE Dozer 1 1 5 1339459200 Yummi!!!! Love this hot cereal! I use 1/3 cup with 1 cup of almond milk, 1 tbsp of flax oil and 1 banana for breakfast (around 400 calories) and it helps me feel full all day! It has definitely decreased my cravings for sugary things. 2012-06-12 List(Love, this, hot, cereal!, I, use, 1/3, cup, with, 1, cup, of, almond, milk,, 1, tbsp, of, flax, oil, and, 1, banana, for, breakfast, (around, 400, calories), and, it, helps, me, feel, full, all, day!, It, has, definitely, decreased, my, cravings, for, sugary, things.) List(love, hot, cereal, use, , cup, , cup, almond, milk, , tbsp, flax, oil, , banana, breakfast, around, , calori, help, feel, full, day, definit, decreas, crave, sugari, thing) 422681 B001LNL0MC A101RJ22EBXAID Disappointed Santa 5 6 1 1295913600 Holeymoley did I order crushed peppermint I ordered 3 boxes of Bob's candy canes because I could not find them in stores near me and I wanted the real thing, Bob's,not Spanglers, to help in the celebration of my father's last Christmas. We wanted an old fashioned, basic heart of America Christmas with him. We were willing to pay almost any price to get original Bob's candy canes for this purpose, hence ordering them at such an inflated price on-line from Amazon. More than half came smashed to smithereens. I sent a note to customer service alerting them to this and heard nothing back. 2011-01-25 List(I, ordered, 3, boxes,

## Saving & Reloading Data

In [18]:
# Save cleaned dataframe back to Azure Data Lake

import json

def array_to_string(my_list):
    return json.dumps(my_list)

array_to_string_udf = udf(array_to_string, StringType())

amazon_review.withColumn('WordList',array_to_string_udf(amazon_review.WordList)) \
             .withColumn('WordListCleaned',array_to_string_udf(amazon_review.WordListCleaned)) \
             .coalesce(1).write.mode("overwrite").format("com.databricks.spark.csv").option("header", "true") \
             .save('abfss://workspace@ssbdatalakegen2.dfs.core.windows.net/reviews_cleaned')

# Move the file out of the temporary folder and rename it

readPath = "abfss://workspace@ssbdatalakegen2.dfs.core.windows.net/reviews_cleaned"
writePath = "abfss://workspace@ssbdatalakegen2.dfs.core.windows.net"
file_list = dbutils.fs.ls(readPath)
for i in file_list:
    file_path = i[0]
    file_name = i[1]

fname = "reviews_cleaned.csv"
for i in file_list:
    if i[1].startswith("part-00000"):
        read_name = i[1]

dbutils.fs.mv(readPath+"/"+read_name, writePath+"/"+fname)

# Delete the empty folder

dbutils.fs.rm(readPath , recurse = True)

In [19]:
# Read the saved dataframe back

amazon_cleaned_schema = StructType([StructField('Id',IntegerType(),True), 
                            StructField('ProductId',StringType(),True),
                            StructField('UserId',StringType(),True),
                            StructField('ProfileName',StringType(),True),
                            StructField('HelpfulnessNumerator',IntegerType(),True),
                            StructField('HelpfulnessDenominator',IntegerType(),True),
                            StructField('Score',IntegerType(),True),
                            StructField('Time',IntegerType(),True),
                            StructField('Summary',StringType(),True),
                            StructField('Text',StringType(),True),
                            StructField('Date',DateType(),True),
                            StructField('WordList',StringType(),True),
                            StructField('WordListCleaned',StringType(),True)])

amazon_review_cleaned = spark.read.csv("abfss://workspace@ssbdatalakegen2.dfs.core.windows.net/reviews_cleaned.csv", header=True, schema=amazon_cleaned_schema)

In [20]:
def string_to_array(my_string):
    return json.loads(my_string)
  
string_to_array_udf = udf(string_to_array,  ArrayType(StringType()))

amazon_review_cleaned = amazon_review_cleaned.withColumn("WordList", string_to_array_udf(amazon_review_cleaned.WordList)) \
                                             .withColumn("WordListCleaned", string_to_array_udf(amazon_review_cleaned.WordListCleaned))

display(amazon_review_cleaned)

Id ProductId UserId ProfileName HelpfulnessNumerator HelpfulnessDenominator Score Time Summary Text Date WordList WordListCleaned 290915 B005HG9ESG #oc-R1OE1OPY34LOC8 D 0 0 3 1344902400 Not the same Been buying this water for a couple of years. They recently changed the packaging and for some reason or other, the water seems different. The same clean taste is just NOT there. Not buying it again. 2012-08-14 List(Been, buying, this, water, for, a, couple, of, years., They, recently, changed, the, packaging, and, for, some, reason, or, other,, the, water, seems, different., The, same, clean, taste, is, just, NOT, there., Not, buying, it, again.) List(buy, water, coupl, year, recent, chang, packag, reason, water, seem, differ, clean, tast, just, buy) 136337 B006Q820X0 #oc-R39HI2LQ9LHV32 stephanie 1 2 1 1339632000 Kcups leaking and coffee tasted old The kcups looked okay, but many of them sprayed coffee on the counter, had coffee grounds coming out. I won't buy this again. 2012-06-14 List(The, kcups, looked, okay,, but, many, of, them, sprayed, coffee, on, the, counter,, had, coffee, grounds, coming, out., I, won't, buy, this, again.) List(kcup, look, okay, mani, spray, coffe, counter, coffe, ground, come, wont, buy) 124400 B005ZBZM52 #oc-R8EZLM74R071X jalien 0 0 1 1350172800 Great design, not so great flavor I wanted to try something new and this is new alright. While I love and appreciate the design, the flavor is less than desirable. It's too bitter. I drink my coffee black and really enjoy a strong cup of dark roast, but after discovering I didn't care for the flavor, I tried to disguise it with the flavor of creamer I knew I'd like (coconut cream, yum) and still the flavor of the bitter coffee was just too much. 2012-10-14 List(I, wanted, to, try, something, new, and, this, is, new, alright., While, I, love, and, appreciate, the, design,, the, flavor, is, less, than, desirable., It's, too, bitter., I, drink, my, coffee, black, and, really, enjoy, a, strong, cup, of, dark, roast,, but, after, discovering, I, didn't, care, for, the, flavor,, I, tried, to, disguise, it, with, the, flavor, of, creamer, I, knew, I'd, like, (coconut, cream,, yum), and, still, the, flavor, of, the, bitter, coffee, was, just, too, much.) List(want, tri, someth, new, new, alright, love, appreci, design, flavor, less, desir, bitter, drink, coffe, black, realli, enjoy, strong, cup, dark, roast, discov, didnt, care, flavor, tri, disguis, flavor, creamer, knew, id, like, coconut, cream, yum, still, flavor, bitter, coffe, just, much) 345714 B000ED9L9E A10103MJIKKIFE Dozer 1 1 5 1339459200 Yummi!!!! Love this hot cereal! I use 1/3 cup with 1 cup of almond milk, 1 tbsp of flax oil and 1 banana for breakfast (around 400 calories) and it helps me feel full all day! It has definitely decreased my cravings for sugary things. 2012-06-12 List(Love, this, hot, cereal!, I, use, 1/3, cup, with, 1, cup, of, almond, milk,, 1, tbsp, of, flax, oil, and, 1, banana, for, breakfast, (around, 400, calories), and, it, helps, me, feel, full, all, day!, It, has, definitely, decreased, my, cravings, for, sugary, things.) List(love, hot, cereal, use, , cup, , cup, almond, milk, , tbsp, flax, oil, , banana, breakfast, around, , calori, help, feel, full, day, definit, decreas, crave, sugari, thing) 422681 B001LNL0MC A101RJ22EBXAID Disappointed Santa 5 6 1 1295913600 Holeymoley did I order crushed peppermint I ordered 3 boxes of Bob's candy canes because I could not find them in stores near me and I wanted the real thing, Bob's,not Spanglers, to help in the celebration of my father's last Christmas. We wanted an old fashioned, basic heart of America Christmas with him. We were willing to pay almost any price to get original Bob's candy canes for this purpose, hence ordering them at such an inflated price on-line from Amazon. More than half came smashed to smithereens. I sent a note to customer service alerting them to this and heard nothing back. 2011-01-25 List(I, ordered, 3, boxes,

## Review Score Prediction

As comparison, without Spark we will use sklearn in Python for machine learning (read more: https://scikit-learn.org/stable/user_guide.html); or NLTK for natural language processing (read more: https://www.nltk.org/)

In [23]:
# Extract bigram

from pyspark.ml.feature import NGram
from pyspark.sql.functions import array_union

ngram = NGram(n = 2, inputCol="WordListCleaned", outputCol="bigram")
amazon_review = ngram.transform(amazon_review)

amazon_review = amazon_review.withColumn("ngrams", array_union(amazon_review.WordListCleaned, amazon_review.bigram))

In [24]:
# Extract 5-star and 1-star reviews for prediction

prediction_df = amazon_review.where((amazon_review.Score == 1) | (amazon_review.Score == 5))
display(prediction_df)

Id ProductId UserId ProfileName HelpfulnessNumerator HelpfulnessDenominator Score Time Summary Text Date WordList WordListCleaned bigram ngrams 136337 B006Q820X0 #oc-R39HI2LQ9LHV32 stephanie 1 2 1 1339632000 Kcups leaking and coffee tasted old The kcups looked okay, but many of them sprayed coffee on the counter, had coffee grounds coming out. I won't buy this again. 2012-06-14 List(The, kcups, looked, okay,, but, many, of, them, sprayed, coffee, on, the, counter,, had, coffee, grounds, coming, out., I, won't, buy, this, again.) List(kcup, look, okay, mani, spray, coffe, counter, coffe, ground, come, wont, buy) List(kcup look, look okay, okay mani, mani spray, spray coffe, coffe counter, counter coffe, coffe ground, ground come, come wont, wont buy) List(kcup, look, okay, mani, spray, coffe, counter, ground, come, wont, buy, kcup look, look okay, okay mani, mani spray, spray coffe, coffe counter, counter coffe, coffe ground, ground come, come wont, wont buy) 124400 B005ZBZM52 #oc-R8EZLM74R071X jalien 0 0 1 1350172800 Great design, not so great flavor I wanted to try something new and this is new alright. While I love and appreciate the design, the flavor is less than desirable. It's too bitter. I drink my coffee black and really enjoy a strong cup of dark roast, but after discovering I didn't care for the flavor, I tried to disguise it with the flavor of creamer I knew I'd like (coconut cream, yum) and still the flavor of the bitter coffee was just too much. 2012-10-14 List(I, wanted, to, try, something, new, and, this, is, new, alright., While, I, love, and, appreciate, the, design,, the, flavor, is, less, than, desirable., It's, too, bitter., I, drink, my, coffee, black, and, really, enjoy, a, strong, cup, of, dark, roast,, but, after, discovering, I, didn't, care, for, the, flavor,, I, tried, to, disguise, it, with, the, flavor, of, creamer, I, knew, I'd, like, (coconut, cream,, yum), and, still, the, flavor, of, the, bitter, coffee, was, just, too, much.) List(want, tri, someth, new, new, alright, love, appreci, design, flavor, less, desir, bitter, drink, coffe, black, realli, enjoy, strong, cup, dark, roast, discov, didnt, care, flavor, tri, disguis, flavor, creamer, knew, id, like, coconut, cream, yum, still, flavor, bitter, coffe, just, much) List(want tri, tri someth, someth new, new new, new alright, alright love, love appreci, appreci design, design flavor, flavor less, less desir, desir bitter, bitter drink, drink coffe, coffe black, black realli, realli enjoy, enjoy strong, strong cup, cup dark, dark roast, roast discov, discov didnt, didnt care, care flavor, flavor tri, tri disguis, disguis flavor, flavor creamer, creamer knew, knew id, id like, like coconut, coconut cream, cream yum, yum still, still flavor, flavor bitter, bitter coffe, coffe just, just much) List(want, tri, someth, new, alright, love, appreci, design, flavor, less, desir, bitter, drink, coffe, black, realli, enjoy, strong, cup, dark, roast, discov, didnt, care, disguis, creamer, knew, id, like, coconut, cream, yum, still, just, much, want tri, tri someth, someth new, new new, new alright, alright love, love appreci, appreci design, design flavor, flavor less, less desir, desir bitter, bitter drink, drink coffe, coffe black, black realli, realli enjoy, enjoy strong, strong cup, cup dark, dark roast, roast discov, discov didnt, didnt care, care flavor, flavor tri, tri disguis, disguis flavor, flavor creamer, creamer knew, knew id, id like, like coconut, coconut cream, cream yum, yum still, still flavor, flavor bitter, bitter coffe, coffe just, just much) 345714 B000ED9L9E A10103MJIKKIFE Dozer 1 1 5 1339459200 Yummi!!!! Love this hot cereal! I use 1/3 cup with 1 cup of almond milk, 1 tbsp of flax oil and 1 banana for breakfast (around 400 calories) and it helps me feel full all day! It has definitely decreased my cravings for sugary things. 2012-06-12 List(Love, this, hot, cereal!, I, use, 1/3, cup, with, 1, cup, of, almond, milk,, 1, tbsp, of, fla

### TF-IDF with Hashing Trick + Random Forest

In [26]:
# Copy prediction data

prediction_tfidf_hash = prediction_df.select('*')

In [27]:
# Getting tf-idf values for 1-2grams

from pyspark.ml.feature import HashingTF, IDF

hashtf = HashingTF(numFeatures=2**12, inputCol="ngrams", outputCol='TF')
tf = hashtf.transform(prediction_tfidf_hash)
idf = IDF(minDocFreq=3, inputCol="TF", outputCol="TF-IDF")
idfModel = idf.fit(tf)
prediction_tfidf_hash = idfModel.transform(tf)

In [28]:
# Random Forest

from pyspark.ml import Pipeline
from pyspark.ml.feature import IndexToString, StringIndexer
from pyspark.ml.classification import RandomForestClassifier

labelIndexer = StringIndexer(inputCol="Score", outputCol="indexedScore").fit(prediction_tfidf_hash)
rf = RandomForestClassifier(labelCol="indexedScore", featuresCol="TF-IDF", numTrees=40)
labelConverter = IndexToString(inputCol="prediction", outputCol="predictedLabel",
                               labels=labelIndexer.labels)

pipeline = Pipeline(stages=[labelIndexer, rf, labelConverter])

(trainingData, testData) = prediction_tfidf_hash.randomSplit([0.7, 0.3])

rf_model = pipeline.fit(trainingData)
predictions = rf_model.transform(testData)


In [29]:
display(predictions.select("Score", "indexedScore", "rawPrediction", "probability", "prediction", "predictedLabel"))

Score indexedScore rawPrediction probability prediction predictedLabel 5 0.0 List(1, 2, List(), List(34.25834695787432, 5.741653042125674)) List(1, 2, List(), List(0.856458673946858, 0.14354132605314185)) 0.0 5 5 0.0 List(1, 2, List(), List(35.311492102774324, 4.6885078972256675)) List(1, 2, List(), List(0.8827873025693582, 0.11721269743064171)) 0.0 5 5 0.0 List(1, 2, List(), List(34.902303655943456, 5.097696344056532)) List(1, 2, List(), List(0.8725575913985867, 0.12744240860141334)) 0.0 5 5 0.0 List(1, 2, List(), List(34.89124611759117, 5.108753882408826)) List(1, 2, List(), List(0.8722811529397794, 0.12771884706022066)) 0.0 5 1 1.0 List(1, 2, List(), List(34.85099831831011, 5.1490016816898985)) List(1, 2, List(), List(0.8712749579577527, 0.12872504204224744)) 0.0 5 5 0.0 List(1, 2, List(), List(35.03872813353971, 4.961271866460284)) List(1, 2, List(), List(0.8759682033384928, 0.1240317966615071)) 0.0 5 5 0.0 List(1, 2, List(), List(35.05945390113855, 4.940546098861447)) List(1, 2, List(), List(0.8764863475284639, 0.12351365247153619)) 0.0 5 5 0.0 List(1, 2, List(), List(34.35419185833013, 5.645808141669868)) List(1, 2, List(), List(0.8588547964582534, 0.1411452035417467)) 0.0 5 5 0.0 List(1, 2, List(), List(35.01350216054717, 4.986497839452833)) List(1, 2, List(), List(0.8753375540136792, 0.12466244598632084)) 0.0 5 5 0.0 List(1, 2, List(), List(35.313246150942064, 4.686753849057935)) List(1, 2, List(), List(0.8828311537735516, 0.11716884622644837)) 0.0 5 5 0.0 List(1, 2, List(), List(35.01350216054717, 4.986497839452833)) List(1, 2, List(), List(0.8753375540136792, 0.12466244598632084)) 0.0 5 5 0.0 List(1, 2, List(), List(35.73193024750933, 4.2680697524906686)) List(1, 2, List(), List(0.8932982561877333, 0.10670174381226671)) 0.0 5 5 0.0 List(1, 2, List(), List(34.94606168744265, 5.053938312557347)) List(1, 2, List(), List(0.8736515421860662, 0.12634845781393367)) 0.0 5 5 0.0 List(1, 2, List(), List(34.87127212820589, 5.128727871794111)) List(1, 2, List(), List(0.8717818032051472, 0.12821819679485277)) 0.0 5 5 0.0 List(1, 2, List(), List(35.16659342735474, 4.833406572645257)) List(1, 2, List(), List(0.8791648356838685, 0.12083516431613142)) 0.0 5 5 0.0 List(1, 2, List(), List(34.64199266928062, 5.358007330719378)) List(1, 2, List(), List(0.8660498167320154, 0.13395018326798444)) 0.0 5 5 0.0 List(1, 2, List(), List(34.19979119840089, 5.800208801599114)) List(1, 2, List(), List(0.8549947799600222, 0.14500522003997784)) 0.0 5 5 0.0 List(1, 2, List(), List(35.366628626962715, 4.633371373037286)) List(1, 2, List(), List(0.8841657156740679, 0.11583428432593215)) 0.0 5 1 1.0 List(1, 2, List(), List(34.97514441805602, 5.024855581943976)) List(1, 2, List(), List(0.8743786104514006, 0.12562138954859942)) 0.0 5 5 0.0 List(1, 2, List(), List(35.046865626357494, 4.953134373642503)) List(1, 2, List(), List(0.8761716406589374, 0.12382835934106258)) 0.0 5 5 0.0 List(1, 2, List(), List(35.046865626357494, 4.953134373642503)) List(1, 2, List(), List(0.8761716406589374, 0.12382835934106258)) 0.0 5 5 0.0 List(1, 2, List(), List(35.11691776248874, 4.883082237511259)) List(1, 2, List(), List(0.8779229440622185, 0.12207705593778147)) 0.0 5 5 0.0 List(1, 2, List(), List(35.187486847607666, 4.812513152392337)) List(1, 2, List(), List(0.8796871711901917, 0.12031282880980843)) 0.0 5 5 0.0 List(1, 2, List(), List(35.78802000286708, 4.211979997132911)) List(1, 2, List(), List(0.8947005000716772, 0.10529949992832281)) 0.0 5 5 0.0 List(1, 2, List(), List(35.11854879140795, 4.88145120859205)) List(1, 2, List(), List(0.8779637197851988, 0.12203628021480124)) 0.0 5 5 0.0 List(1, 2, List(), List(35.11691776248874, 4.883082237511259)) List(1, 2, List(), List(0.8779229440622185, 0.12207705593778147)) 0.0 5 5 0.0 List(1, 2, List(), List(35.14466031475383, 4.855339685246167)) List(1, 2, List(), List(0.8786165078688458, 0.12138349213115421)) 0.0 5 5 0.0 List(1, 2, List(), List(34.83549108469386, 5.164508915306146)) List(1, 2, List(), List(0.8708872771173464, 0.1

In [30]:
# Calculate AUC for train/test split

from pyspark.ml.evaluation import BinaryClassificationEvaluator

evaluator = BinaryClassificationEvaluator(labelCol="indexedScore", metricName="areaUnderROC")
auc = evaluator.evaluate(predictions)
print("AUC = %g" % auc)

AUC = 0.830661

In [31]:
# Performance evaluation with 10-fold cross validation

from pyspark.ml.tuning import CrossValidator, ParamGridBuilder
paramGrid = ParamGridBuilder().build()
cv = CrossValidator(estimator=pipeline, evaluator=evaluator, estimatorParamMaps=paramGrid, numFolds=10)
cvModel = cv.fit(prediction_tfidf_hash)

In [32]:
print("Average AUC = %g" % cvModel.avgMetrics[0])

Average AUC = 0.811377

### Doc2Vec + Random Forest

In [34]:
# Copy prediction data

prediction_doc2vec = prediction_df.select('*')

In [35]:
# Calculate Doc2Vec

from pyspark.ml.feature import Word2Vec

word2Vec = Word2Vec(inputCol="WordListCleaned", outputCol="doc2vec")
w2v_model = word2Vec.fit(prediction_doc2vec)

prediction_doc2vec = w2v_model.transform(prediction_doc2vec)

In [36]:
display(prediction_doc2vec)

Id ProductId UserId ProfileName HelpfulnessNumerator HelpfulnessDenominator Score Time Summary Text Date WordList WordListCleaned bigram ngrams doc2vec 136337 B006Q820X0 #oc-R39HI2LQ9LHV32 stephanie 1 2 1 1339632000 Kcups leaking and coffee tasted old The kcups looked okay, but many of them sprayed coffee on the counter, had coffee grounds coming out. I won't buy this again. 2012-06-14 List(The, kcups, looked, okay,, but, many, of, them, sprayed, coffee, on, the, counter,, had, coffee, grounds, coming, out., I, won't, buy, this, again.) List(kcup, look, okay, mani, spray, coffe, counter, coffe, ground, come, wont, buy) List(kcup look, look okay, okay mani, mani spray, spray coffe, coffe counter, counter coffe, coffe ground, ground come, come wont, wont buy) List(kcup, look, okay, mani, spray, coffe, counter, ground, come, wont, buy, kcup look, look okay, okay mani, mani spray, spray coffe, coffe counter, counter coffe, coffe ground, ground come, come wont, wont buy) List(1, 100, List(), List(-0.11070514687647422, 0.07480503991246223, -0.09966146717003235, -0.05415507995833953, 0.09616886296619971, 0.04276601869302491, 0.001795660345427071, -0.011994701509441558, -0.001392077732210358, -0.06035017354103426, 0.06006408979495366, 0.06617037571656206, 0.04775558963107566, 0.0875061034845809, -0.0203114782149593, 0.02688704834630092, -0.02852808559934298, 0.008171051376848482, -0.00893517614652713, -0.0013350746594369411, -0.0871660765260458, -0.03036282939137891, -0.01140535343438387, -0.12211513488243023, 0.014471503750731547, -0.06954166983875135, -0.030523703123132385, -0.035681207974751786, -0.06845997211833794, 0.1751752517496546, -0.003685681770245234, -0.10145162728925546, 0.04248712809445957, -0.008931353125565995, -0.009937205914563188, 0.1514523564837873, 0.08226896659471095, 0.07908314187079668, 0.02311551348248031, -0.03882682118273806, -0.060955917462706566, 0.02854286708558599, 0.07569438715775807, -0.03359428715581695, 0.08153154204289118, 0.0771238449960947, 0.03548233529242376, 0.0148899732157588, 0.09837541806822021, -0.009523687496160466, 0.059004973309735455, -0.0509311967374136, 0.13392736731717983, 0.0011397929241259892, -0.023425499520575006, 0.007224394008517265, 0.16732169974905747, -0.12265889534804349, -0.10192612818597505, -0.11927961573625603, 0.09015046712011099, -0.13455304130911827, 0.01785769717146953, 0.0785536131200691, -0.0651134136132896, -0.003634004659640292, 0.18758404805945852, 0.047738587561373905, 0.04151505387077729, 0.053369783563539386, -0.2371798498982874, -0.17362718128909665, 0.07997869079311688, -0.006412364232043425, -0.06205862512191136, 0.02315822437716027, 0.05182298528961837, 0.010251031257212162, -0.06294083238268891, 0.02299553466339906, 0.08857928883905211, 0.17570667279263336, -0.1250551516811053, 0.013432381713452438, 0.0243382448485742, -0.0057703068911602404, 0.05804337561130524, 0.06014510989189148, -0.10078359449592729, -0.023347922775428742, 0.14351562620140612, 0.08410788055819769, -0.18434194196015596, -2.619049822290738E-4, -0.15106081838409105, 0.06801097933202982, 0.025421484373509884, -0.00783106591552496, -0.11268715199548751, -0.02298047083119551)) 124400 B005ZBZM52 #oc-R8EZLM74R071X jalien 0 0 1 1350172800 Great design, not so great flavor I wanted to try something new and this is new alright. While I love and appreciate the design, the flavor is less than desirable. It's too bitter. I drink my coffee black and really enjoy a strong cup of dark roast, but after discovering I didn't care for the flavor, I tried to disguise it with the flavor of creamer I knew I'd like (coconut cream, yum) and still the flavor of the bitter coffee was just too much. 2012-10-14 List(I, wanted, to, try, something, new, and, this, is, new, alright., While, I, love, and, appreciate, the, design,, the, flavor, is, less, than, desirable., It's, too, bitter., I, drink, my, coffee, black, and, really, enjoy, a, strong, cup, of, dark, roast,, but, after, discovering, I, didn't, care, f

In [37]:
# Random Forest

from pyspark.ml import Pipeline
from pyspark.ml.feature import IndexToString, StringIndexer
from pyspark.ml.classification import RandomForestClassifier

labelIndexer = StringIndexer(inputCol="Score", outputCol="indexedScore").fit(prediction_doc2vec)
rf = RandomForestClassifier(labelCol="indexedScore", featuresCol="doc2vec", numTrees=40)
labelConverter = IndexToString(inputCol="prediction", outputCol="predictedLabel",
                               labels=labelIndexer.labels)

pipeline = Pipeline(stages=[labelIndexer, rf, labelConverter])

(trainingData, testData) = prediction_doc2vec.randomSplit([0.7, 0.3])

rf_model = pipeline.fit(trainingData)
predictions = rf_model.transform(testData)

from pyspark.ml.evaluation import BinaryClassificationEvaluator

evaluator = BinaryClassificationEvaluator(labelCol="indexedScore", metricName="areaUnderROC")
auc = evaluator.evaluate(predictions)
print("AUC = %g" % auc)

AUC = 0.893713

In [38]:
# Performance evaluation with 10-fold cross validation

from pyspark.ml.tuning import CrossValidator, ParamGridBuilder

paramGrid = ParamGridBuilder().build()
cv = CrossValidator(estimator=pipeline, evaluator=evaluator, estimatorParamMaps=paramGrid, numFolds=10)
cvModel = cv.fit(prediction_doc2vec)

print("Average AUC = %g" % cvModel.avgMetrics[0])

/databricks/spark/python/pyspark/ml/util.py:791: UserWarning: Can not find mlflow. To enable mlflow logging, install MLflow library from PyPi.
 warnings.warn(_MLflowInstrumentation._NO_MLFLOW_WARNING)
Average AUC = 0.891858

## Model Interpretation

In [40]:
# Calculating TF-IDF without hashing; limit vocabulary to top 2^12 (4096) ngrams

from pyspark.ml.feature import CountVectorizer, IDF

interpret_tfidf = prediction_df.select('*')

tf = CountVectorizer(inputCol="ngrams", outputCol='TF', minDF=2.0, vocabSize=2**12)
tf_model = tf.fit(interpret_tfidf)
tf_transformed = tf_model.transform(interpret_tfidf)
idf = IDF(minDocFreq=3, inputCol="TF", outputCol="TF-IDF")
idfModel = idf.fit(tf_transformed)
interpret_tfidf = idfModel.transform(tf_transformed)

In [41]:
# Building a full Random Forest model with all the data, using TF-IDF embedding without hashing

from pyspark.ml import Pipeline
from pyspark.ml.feature import IndexToString, StringIndexer
from pyspark.ml.classification import RandomForestClassifier

labelIndexer = StringIndexer(inputCol="Score", outputCol="indexedScore").fit(interpret_tfidf)
rf = RandomForestClassifier(labelCol="indexedScore", featuresCol="TF-IDF", numTrees=40)
labelConverter = IndexToString(inputCol="prediction", outputCol="predictedLabel",
                               labels=labelIndexer.labels)

pipeline = Pipeline(stages=[labelIndexer, rf, labelConverter])

rf_model = pipeline.fit(interpret_tfidf)

In [42]:
# Getting feature importance from the Random Forest model

feature_importance = rf_model.stages[-2].featureImportances
print(feature_importance)

(4096,[0,1,2,3,4,5,7,8,9,10,11,12,13,14,16,17,18,19,21,23,24,25,26,27,29,30,31,32,33,34,35,36,37,39,41,45,46,49,50,51,53,54,56,57,58,59,60,61,63,65,67,70,71,72,75,78,79,80,81,82,84,85,86,88,89,92,94,95,98,100,101,102,105,107,109,110,111,113,115,116,117,120,122,123,126,127,128,130,131,132,133,135,136,139,142,143,146,147,148,149,155,156,157,163,168,169,173,180,183,185,186,191,193,194,200,202,203,205,206,208,210,211,213,214,215,218,220,221,224,225,226,227,230,231,233,236,239,240,243,244,246,249,251,253,254,255,257,259,266,267,270,271,275,290,295,301,306,308,309,310,319,323,326,330,333,334,338,343,347,352,355,359,363,365,371,372,383,387,396,398,404,406,413,417,418,421,422,426,429,430,439,440,443,444,446,451,454,461,464,465,476,479,481,489,491,492,493,498,499,505,507,510,511,512,513,519,523,528,531,542,544,546,553,558,561,564,565,567,571,578,583,587,594,598,602,617,622,628,639,641,652,653,661,665,669,674,683,685,686,687,689,698,704,706,715,716,720,722,723,724,726,741,743,748,750,756,758,767,778,786,787,792,796,798,802,810,812,823,833,834,836,837,841,844,848,857,863,865,866,895,897,898,909,924,925,930,946,949,950,957,962,983,996,999,1015,1025,1027,1030,1031,1033,1036,1046,1052,1053,1055,1068,1085,1089,1096,1114,1120,1125,1145,1148,1151,1153,1156,1158,1162,1164,1166,1170,1175,1178,1181,1186,1201,1203,1205,1206,1217,1229,1241,1242,1246,1264,1268,1283,1285,1291,1297,1305,1318,1327,1332,1346,1353,1358,1362,1366,1367,1380,1381,1385,1398,1403,1405,1408,1415,1422,1441,1454,1479,1487,1493,1498,1499,1521,1522,1553,1569,1580,1584,1591,1610,1618,1623,1651,1659,1662,1674,1681,1706,1707,1708,1719,1720,1734,1735,1736,1741,1746,1766,1769,1772,1806,1817,1819,1825,1834,1838,1858,1863,1869,1871,1872,1874,1882,1883,1888,1889,1893,1901,1909,1912,1933,1968,2025,2046,2052,2056,2059,2072,2084,2094,2113,2124,2129,2131,2169,2176,2189,2232,2260,2268,2323,2324,2329,2335,2349,2350,2351,2368,2424,2450,2452,2455,2495,2508,2518,2543,2557,2593,2642,2643,2646,2658,2668,2707,2716,2722,2742,2746,2753,2761,2767,2769,2792,2821,2834,2837,2861,2862,2900,2904,2909,2921,2949,2953,2956,2958,2972,2993,3004,3009,3030,3033,3042,3049,3097,3119,3145,3155,3158,3208,3210,3226,3229,3238,3249,3260,3263,3272,3293,3302,3328,3336,3339,3344,3354,3381,3399,3409,3429,3459,3468,3500,3528,3549,3613,3624,3683,3745,3777,3824,3826,3829,3848,3850,3858,3869,3892,3902,3904,3912,3931,3940,3941,3994,4017,4018,4025,4051,4053,4060],[0.0001388236428043824,0.0049049915267804405,3.926608587119645e-06,0.00019937286724269312,0.007101364276497856,0.004759869066905917,0.0012932881897993955,0.00017456820974391676,0.01401970680648223,2.3808102998252715e-05,0.00032326224049769576,2.8462335200871657e-05,2.744172285935041e-05,9.40493247029107e-05,0.0024402995422870663,0.00025862993509926226,0.009942104671565501,0.00024078094273098633,0.0017603030981187717,3.4354369283438155e-05,0.0003051657296418386,0.0006127121071284735,0.0036590534309227057,0.0013914198456481221,0.0002001763008930946,4.771443941591726e-05,0.00024629805478238093,4.6769132340344676e-05,0.00010007974430869745,0.0005725457996049502,7.429706691661903e-05,0.0001859917957547686,0.0005682783037976658,0.00017922004069197977,0.0002895951415877428,0.0006186010886372044,0.00016542691454196826,0.00026731940793511426,0.0023599691495249276,0.00039496988527756713,0.003427793264327931,0.02183626575110121,0.00026225510513514254,2.4610967412048903e-05,0.0002796196004517657,8.546432643599008e-05,0.00012088534763269596,0.0013132711475657747,0.0012524761098827517,3.3886557559031626e-05,0.001532500416446934,0.00010141693795544368,0.0011104195634153023,7.597689121503244e-05,0.0002444596573170752,0.0020076051046843315,1.1476097037863037e-05,0.0003108925562541003,0.004310317161950275,0.005772875719781259,0.000278645900001052,5.0874577053097934e-05,0.0008568469141898623,0.010456077917294823,1.0401421273046326e-05,0.0015766950753207127,1.2142620186980444e-05,0.0009203126738019116,3.560079311402637e-05,3.808239366619838e-05,0.0006727315547761713,4.919199257129737e-05,2.20

In [43]:
# Get the top 20 most important feature's indices, and its importance metric

import numpy as np
import pandas as pd

top20_indice = np.flip(np.argsort(feature_importance.toArray()))[:20].tolist()
top20_importance = []
for index in top20_indice:
    top20_importance.append(feature_importance[index])

top20_df = spark.createDataFrame(pd.DataFrame(list(zip(top20_indice, top20_importance)), columns =['index', 'importance']))

display(top20_df)

index importance 930 0.09553667130565502 510 0.07714502457160137 715 0.07582302652521568 218 0.03575261357590545 1027 0.03300056372109557 440 0.0314459798847877 1706 0.03139210962348484 1229 0.030599263977690694 54 0.02183626575110121 1120 0.02085154470724603 1096 0.02027602568811518 2837 0.019778362017761942 2593 0.017328284679721036 1362 0.01729699588706808 2368 0.01574116411981894 3850 0.015535362114038328 844 0.015370909052512982 9 0.01401970680648223 1366 0.013147293586948465 1283 0.012974957054432542

In [44]:
# Create a map between each ngram and its index

from pyspark.sql.functions import explode, udf

make_list_udf = udf(lambda col: [col], ArrayType(StringType()))
remove_list_udf = udf(lambda col: col[0], StringType())

def get_index(col):
  if len(col.indices) == 0:
    return -1   # Mark the ngram's index as -1 if it is not the top 2^12 ngrams
  else:
    return int(col.indices[0])
get_index_udf = udf(get_index, IntegerType())

ngram_index = interpret_tfidf.select(explode(interpret_tfidf.ngrams).alias("ngrams")).distinct() \
                             .withColumn("ngrams", make_list_udf("ngrams"))
ngram_index = tf_model.transform(ngram_index)
ngram_index = ngram_index.withColumn("ngrams", remove_list_udf("ngrams")) \
                         .withColumn("index", get_index_udf("TF")) \
                         .select("ngrams", "index")

In [45]:
display(ngram_index.where(ngram_index.index > -1))

ngrams index still 100 yummi 352 dri 145 habanero 3821 gloria 2971 small amount 1702 far 3398 everyday 879 earl 1266 buy one 2032 travel 782 hope 254 spoil 1612 imagin 868 harder 2044 huge fan 2502 pitcher 3830 product one 2744 product realli 3087 cramp 2742 mix make 3540 trail 3641 definit 3200 highest 2535 like littl 2820 goe 386 clearli 1782 fructos corn 2387 dog realli 4021 drink water 2782 local store 573 often 408 bone 701 import 738 oliv 688 malt 3482 water tast 3103 also help 3275 first cup 2647 hairbal 3392 crust 1771 like flavor 1198 arriv quickli 1639 awhil 1601 ad sugar 2193 drain 2384 just put 3285 dough 2562 coffe realli 3706 next day 1641 cook 170 watch 641 vinegar 934 give 3278 read label 4075 equal 1235 like get 3353 christma gift 2790 bad tast 3165 healthi snack 1237 butter flavor 3106 drip 2305 sardin 3350 per day 2158 explain 2437 time manner 2989 tri 8 jar 414 intact 3479 husband like 3590 cat food 553 definit buy 1131 cardboard 1515 slow 2003 agre 717 prevent 1628 stomach 471 ye 514 itali 2530 farm 1430 valley 3385 stove 2682 store buy 3817 love cereal 3721 one review 2986 tast one 2596 first 1640 stori 2338 one star 3042 dozen 1856 thick 667 grow 964 choic 420 larabar 3588 soooo 2420 artifici sweeten 1795 full flavor 1531 buy brand 3533 melt mouth 2560 tast test 3216 boost 1271 decis 3384 textur tast 3446 like mani 2534 start day 2071 day 41 found amazon 1280 tast realli 1510 consid 554 find good 2249 intend 2140 among 1721 strong coffe 1532 fabul 1104 favorit treat 3091 smoother 3487 dog 1429 experienc 1661 food item 3336 fatti 3450 anyth els 1158 pickl 3303 joint 2836 subject 4064 like well 3388 even 30 breakfast blend 2577 happen 613 good qualiti 1210 tri one 1073 mani peopl 2589 bc 3131 will eat 789 biscuit 1304 coffe maker 1059 goodi 3402 like coffe 1039 hot chocol 1072 get sick 3021 didnt know 2482 breed 1912 gotta 3105 never get 3418 rais 1949 whether 1251 got 87 space 2083 ahead 1758 mountain 803 ever tri 1594 throughout 1748 product made 2762 sticki 1609 earlier 2336 small dog 2231 sweet 2388 much like 1707 now get 3781 coffe good 1934 two 72 extra 278 local 94 us 207 without bitter 2507 odd 1883 meat 376 counter 1685 sunflow 2369 coffe machin 4024 carri product 3956 expir 844 product tri 2449 realli tasti 3648 milder 3644 resembl 3764 dont use 2277 great servic 3364 wont buy 2837 realli 23 present 1103 discount 1530 can 1831 lack 1252 month old 771 hit 532 promptli 1516 low calori 1119 mug 1383 fishi 3136 folk 1499 complex 1976 product excel 3407 blend coffe 3933 affect 2220 never go 2927 excel flavor 3624 teaspoon 3383 odor 1806 stock 381 tend 855 berri 970 restrict 3653 great flavor 675 hot cocoa 2202 sensit 801 tub 2415 caffein free 3905 mint 802 larger size 4050 munch 2162 batter 3555 great gift 3001 love coffe 1021 father 2668 childhood 2295 bought 2434 slightli sweet 3400 x 1882 tray 3146 decad 2031 econom 1813 better deal 3132 well can 3845 seattl 3991 make wonder 2672 honey 388 lunch 530 free 3077 great 1276 choke 2017 act 2406 can also 1852 orang 702 found local 3524 ps 3250 wrote 2905 will last 1698 like tri 2838 sushi 3643 feel guilti 3224 cup hot 3702 celiac diseas 3064 within 577 big hit 3568 fond 3448 subscript 995 one 787 rich 267 puff 2412 burn 1146 neg review 3315 san 2205 cold water 3768 dash 3651 great tea 2670 blood sugar 2092 shame 2124 disappear 1817 white chocol 3040 theyd 3255 buy 16 littl 34 set 506 quantiti 856 plain 467 perfect 81 vanilla 328 length 3770 coupl week 3476 food dog 1919 toward 2819 case 2311 cooki 3508 account 4082 your look 1877 teeth clean 2737 ive found 1015 chai tea 1984 singl serv 2055 eat lot 3228 somehow 2508 regardless 3463 flower 1632 quaker 2570 magnesium 2746 wet 923 mustard 1729 scienc diet 1838 one dog 2148 kernel 2348 new york 4005 greatest 3369 andor 1697 releas 4051 bit pricey 2825 liter 1018 one good 3435 joy 2938 cupcak 3043 per 3093 inch 2118 past 2381 just cant 2537 constant 3305 amazon best 2307 fragranc 3267 fact 262 wont disappoint

In [46]:
# Find the ngrams that map to the top 20 most important features

# Note that if you used hashingTF for word embedding, there would be multiple ngrams under the same index, because of the collision introduced by hashing, all of which would share and contribute to one importance score, and we don't have a way to separate their contribution to the importance score.
# Here in order to avoid such collision (so just one index per ngram), I used CountVectorizer instead of HashingTF during encoding.

import pyspark.sql.functions as f

top20_ngram = top20_df.join(ngram_index, on="index", how="left_outer")
display(top20_ngram.groupby("importance").agg(f.collect_list(top20_ngram.ngrams).alias("ngram")).orderBy("importance", ascending=False))

importance ngram 0.09553667130565502 List(worst) 0.07714502457160137 List(return) 0.07582302652521568 List(horribl) 0.03575261357590545 List(money) 0.03300056372109557 List(wast money) 0.0314459798847877 List(wast) 0.03139210962348484 List(never buy) 0.030599263977690694 List(disgust) 0.02183626575110121 List(delici) 0.02085154470724603 List(china) 0.02027602568811518 List(threw) 0.019778362017761942 List(wont buy) 0.017328284679721036 List(dont wast) 0.01729699588706808 List(mistak) 0.01574116411981894 List(throw away) 0.015535362114038328 List(tast aw) 0.015370909052512982 List(expir) 0.01401970680648223 List(product) 0.013147293586948465 List(refund) 0.012974957054432542 List(gross)